# Team 4_4_Graph_Feature

In [0]:
# Setup
!pip install networkx

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
dbutils.library.restartPython()

In [0]:
# imports
from graphframes import GraphFrame
from pyspark.sql.functions import col
import re
import heapq
import itertools
import numpy as np
import networkx as nx # 
from collections import defaultdict, deque
import matplotlib.pyplot as plt
%matplotlib inline

In [0]:

data_BASE_DIR = "dbfs:/mnt/mids-w261/"
# Team folder
section = "4"
number = "4"
folder_path = f"dbfs:/student-groups/Group_{section}_{number}"
data_path_12M = f"{folder_path}/data_12M/"


df_1Y_features = spark.read.parquet(f"{data_path_12M}/df_joined_1Y_2015_features.parquet/")

print(f"Our feature dataset has {df_1Y_features.count()} rows and {len(df_1Y_features.columns)} columns.") 

# print the first 5 rows
display(df_1Y_features.limit(5))


Our feature dataset has 14536464 rows and 47 columns.


ORIGIN MONTH flight_id prediction_utc origin_obs_utc asof_minutes FL_DATE YEAR QUARTER DAY_OF_MONTH DAY_OF_WEEK OP_CARRIER OP_CARRIER_FL_NUM TAIL_NUM CRS_DEP_TIME DEST DISTANCE DISTANCE_GROUP HourlyDryBulbTemperature HourlyDewPointTemperature HourlyWetBulbTemperature HourlyPrecipitation HourlyWindSpeed HourlyWindDirection HourlyVisibility HourlyRelativeHumidity HourlyStationPressure HourlySeaLevelPressure HourlyAltimeterSetting HourlySkyConditions ORIGIN_TYPE DEST_TYPE DEP_DEL15 DEP_DELAY DEP_HOUR DEP_MINUTE dep_time_bucket is_weekend peak_travel_month peak_travel_hour is_holiday dep_delay_24h_rolling_avg_by_origin dep_delay15_24h_rolling_avg_by_origin dep_delay_24h_rolling_avg_by_origin_carrier dep_delay15_24h_rolling_avg_by_origin_carrier dep_delay_24h_rolling_avg_by_origin_dayofweek dep_delay15_24h_rolling_avg_by_origin_dayofweek AKN 6 2019-06-10|AS|163|AKN|ANC 2019-06-10T23:50:00Z 2019-06-10T22:54:00Z 56 2019-06-10 2019 2 10 1 AS 163 N403AS 1750 ANC 288.0 2 54.0 45.0 49.0 0.0 3.0 240.0 10.0 72.0 29.84000015258789 29.8799991607666 29.889999389648438 41.0 medium_airport large_airport 0.0 2.0 17 50 evening 0 1 1 0 0.0 0.0 0.0 0.0 -3.6 0.016666666666666666 AKN 6 2019-06-10|AS|163|AKN|ANC 2019-06-10T23:50:00Z 2019-06-10T22:54:00Z 56 2019-06-10 2019 2 10 1 AS 163 N403AS 1750 ANC 288.0 2 54.0 45.0 49.0 0.0 3.0 240.0 10.0 72.0 29.84000015258789 29.8799991607666 29.889999389648438 41.0 medium_airport large_airport 0.0 2.0 17 50 evening 0 1 1 0 0.0 0.0 0.0 0.0 -3.6 0.016666666666666666 AKN 6 2019-06-17|AS|163|AKN|ANC 2019-06-17T23:50:00Z 2019-06-17T22:54:00Z 56 2019-06-17 2019 2 17 1 AS 163 N565AS 1750 ANC 288.0 2 55.0 50.0 52.0 0.0 8.0 200.0 10.0 83.0 29.639999389648438 29.690000534057617 29.690000534057617 41.0 medium_airport large_airport 0.0 -7.0 17 50 evening 0 1 1 0 -6.0 0.0 -6.0 0.0 -3.6 0.016666666666666666 AKN 6 2019-06-17|AS|163|AKN|ANC 2019-06-17T23:50:00Z 2019-06-17T22:54:00Z 56 2019-06-17 2019 2 17 1 AS 163 N565AS 1750 ANC 288.0 2 55.0 50.0 52.0 0.0 8.0 200.0 10.0 83.0 29.639999389648438 29.690000534057617 29.690000534057617 41.0 medium_airport large_airport 0.0 -7.0 17 50 evening 0 1 1 0 -6.0 0.0 -6.0 0.0 -3.6 0.016666666666666666 AKN 6 2019-06-24|AS|163|AKN|ANC 2019-06-24T23:50:00Z 2019-06-24T22:54:00Z 56 2019-06-24 2019 2 24 1 AS 163 N517AS 1750 ANC 288.0 2 53.0 50.0 51.0 0.0 7.0 260.0 10.0 89.0 29.959999084472656 30.010000228881836 30.010000228881836 41.0 medium_airport large_airport 0.0 -11.0 17 50 evening 0 1 1 0 -1.0 0.0 -1.0 0.0 -3.6 0.016666666666666666

We will design our graph database with airports as the nodes and the flights as the edges.  The number of flights originating from an airport will be its attribute. The number of flights reaching an airport will also be its attributes. 

In [0]:
edges = (
    df_1Y_features
    .groupBy("ORIGIN", "DEST")
    .count()
    .withColumnRenamed("ORIGIN", "src")
    .withColumnRenamed("DEST", "dst")
    .withColumnRenamed("count", "weight")
)


# count of number of edges
print(f"There are {edges.count()} edges in our graph.")

#display edges sorted by distance
display(edges.orderBy(col("weight").desc()), limit=10)

There are 6515 edges in our graph.


src dst weight LGA ORD 28338 ORD LGA 28216 LAX SFO 28176 SFO LAX 28172 LAX JFK 25502 JFK LAX 25396 LAX LAS 23234 LAS LAX 23224 HNL OGG 21442 OGG HNL 21434 LGA BOS 19820 BOS LGA 19708 LGA ATL 18730 ATL LGA 18672 MCO ATL 18538 ATL MCO 18462 SFO SEA 18342 SEA SFO 18332 ATL FLL 17230 FLL ATL 17200 LAX SEA 17182 SEA LAX 17140 DCA BOS 17126 BOS DCA 17084 LAX ORD 15694 ORD LAX 15694 HNL KOA 15602 KOA HNL 15584 DCA ORD 15472 ORD DCA 15464 SFO LAS 15354 LAS SFO 15300 PHX DEN 15286 DEN PHX 15232 ATL ORD 15150 JFK SFO 15086 SFO JFK 15082 ORD ATL 15010 PHL BOS 14992 BOS ORD 14992 ORD BOS 14968 BOS PHL 14916 DFW ORD 14804 ORD DFW 14780 SFO SAN 14650 MSP ORD 14602 ORD MSP 14582 SAN SFO 14572 DEN LAX 14458 DFW LAX 14396 SEA ANC 14388 LAX DEN 14376 LAX DFW 14348 TPA ATL 14302 ATL TPA 14288 ATL DCA 14030 DCA ATL 14028 ANC SEA 13918 SEA LAS 13902 LAS SEA 13886 ATL MIA 13880 MIA ATL 13878 DEN SLC 13876 HNL LIH 13866 LIH HNL 13864 SLC DEN 13802 LAS DEN 13632 SEA DEN 13574 EWR MCO 13558 DEN LAS 13528 MCO EWR 13524 DEN SEA 13522 DFW ATL 13478 ATL BWI 13478 ATL DFW 13462 BWI ATL 13384 ORD DTW 13226 LAX PHX 13182 DTW ORD 13172 PHX LAX 13066 ATL EWR 12926 EWR ATL 12918 ATL LAX 12820 DCA LGA 12790 LGA DCA 12786 ATL PHL 12752 PHL ATL 12724 LGA DFW 12722 DFW LGA 12712 SAN SJC 12648 CLT ATL 12610 SJC SAN 12608 LAX ATL 12560 BOS ATL 12548 ATL CLT 12534 ATL BOS 12522 ORD SFO 12496 SFO ORD 12442 ORD DEN 12360 DEN ORD 12340 PHX SEA 12326 SEA PHX 12298 DAL HOU 12092 HOU DAL 12076 DEN ATL 11904 DFW IAH 11880 IAH DFW 11874 ATL DEN 11822 SAN SMF 11696 LAX HNL 11696 SMF SAN 11688 HNL LAX 11664 DEN MSP 11490 DEN DFW 11478 DFW DEN 11472 EWR SFO 11466 LGA CLT 11446 MCO PHL 11436 SFO EWR 11430 MSP DEN 11414 PHL MCO 11414 CLT LGA 11410 LGA MIA 11274 MIA LGA 11220 SFO DEN 11162 ORD SEA 11154 BOS EWR 11154 SEA ORD 11146 EWR BOS 11146 LAX SLC 11118 DEN SFO 11034 SLC LAX 11020 PHX LAS 10900 SAN PHX 10868 PHX SAN 10842 BOS BWI 10820 LAS PHX 10806 BWI BOS 10778 CVG ORD 10762 EWR ORD 10750 ORD CVG 10740 ORD EWR 10706 JFK BOS 10678 ATL MSY 10654 ATL RDU 10578 BOS JFK 10566 IAH ATL 10554 MSY ATL 10548 RDU ATL 10542 ORD PHX 10532 ATL IAH 10520 PHX ORD 10508 MCO SJU 10402 JAX ATL 10378 ATL JAX 10374 SJU MCO 10350 ORD BNA 10344 BOS LAX 10300 LAX BOS 10256 ATL DTW 10252 BNA ORD 10232 DTW ATL 10208 SJC SNA 10198 ORD IAH 10192 HNL ITO 10190 ITO HNL 10178 IAH ORD 10176 PDX SFO 10084 SNA SJC 10074 LAX PDX 10044 SFO BOS 10026 SFO PDX 10016 DFW LAS 9984 BNA ATL 9968 BOS SFO 9966 LAX SJC 9944 LAS DFW 9942 ATL BNA 9940 ORD PHL 9908 ORD CLE 9898 PDX LAX 9892 SJC LAX 9882 LAS SAN 9880 PHL ORD 9820 EWR LAX 9810 CLE ORD 9802 FLL EWR 9802 LGA DTW 9790 EWR FLL 9788 ORD CMH 9770 CMH ORD 9768 LAX EWR 9758 CLT ORD 9744 DTW LGA 9738 SAN LAS 9698 SJC SEA 9696 ORD CLT 9678 LAX OAK 9652 SEA SJC 9648 SAN SEA 9640 SEA SAN 9620 SFO PHX 9594 ORD IND 9590 ORD LAS 9588 OAK LAX 9580 LAS ORD 9548 PHX SFO 9542 LGA FLL 9532 EWR CLT 9530 FLL LGA 9510 CLT EWR 9490 LAS OAK 9430 OAK LAS 9426 LGA RDU 9418 RDU LGA 9398 SMF LAX 9392 ORD MCO 9392 ATL LAS 9384 MCO ORD 9380 LAS ATL 9362 LAX SMF 9308 IAH LAX 9284 LAX IAH 9268 IAH DEN 9252 DEN IAH 9250 ATL MSP 9186 MSP ATL 9172 LGA BNA 9130 DFW PHX 9078 IND ORD 9070 BNA LGA 9068 PHX DFW 9046 DFW SFO 9030 JFK MCO 9028 MCO JFK 9006 LGA CLE 8956 SFO DFW 8946 CLE LGA 8944 DEN SAN 8920 SAN DEN 8866 ATL IAD 8742 IAD ATL 8656 PIT LGA 8656 SJC BUR 8652 MCO DFW 8650 DFW MCO 8650 LGA PIT 8638 MDW MSP 8608 BUR SJC 8602 MCO BOS 8560 SLC PHX 8542 MSP MDW 8528 BOS MCO 8524 PHX SLC 8514 MCO BWI 8502 LGA DEN 8492 ATL RIC 8484 RIC ATL 8478 DEN LGA 8452 BWI MCO 8412 IND ATL 8390 ATL IND 8388 DFW MSP 8388 FLL BWI 8374 MSP DFW 8364 BWI FLL 8338 ATL MDW 8320 BOS CLT 8320 LGA IAH 8312 IAH LGA 8304 OAK BUR 8280 MDW ATL 8272 CLT BOS 8268 DEN AUS 8214 HOU ATL 8208 BUR OAK 8204 PBI ATL 8192 CLT MCO 8166 STL ATL 8160 PHX SNA 8160 MCO CLT 8154 SNA PHX 8152 ATL PBI 8144 ATL STL 8114 ATL HOU 8080 ORD MIA 8064 LAX AUS 8058 AUS DEN 8052 SEA SLC 8034 MIA ORD 8034 DFW SEA 8030 SEA DFW 8028 CLT BWI 8020 BWI 

In [0]:
vertices = df_1Y_features.select("ORIGIN").distinct().withColumnRenamed("ORIGIN", "id").union(df_1Y_features.select("DEST").distinct().withColumnRenamed("DEST", "id"))

# count of number of nodes
print(f"There are {vertices.count()} nodes in our graph.")

display(vertices, limit=10)


There are 720 nodes in our graph.


id BKG BWI TPA APN CMX PRC OKC ROA BRW OTH SMF SPI SFB ABI BFF ELM MBS ABR DVL FCA PHX ABY BET PWM STL ABE DFW MHT TXK BFM GSP LSE MMH FAY STX HDN GUC EKO LBB CRP EGE HVN CHA DTW HOU TYS ADQ YUM FWA MDT ONT JAX STS HTS LAX MOT MSP BGR BTR SIT AGS MCO OTZ ROC SGF WYS MCI PIR FLG GRK BNA CGI CLL CLT PAE TVC BLI PSC ORH ABQ PBI PIE ART SDF ACV LAW SCK BDL DAL ITH MRY DBQ USA CLE ACK PDX MFR MIA TWF FSD SWF BQK CSG SUN SFO MEM SAF ELP BHM ATL FLL FNT PIH AZA AKN RIC LCK DAY PHF OMA SJT LCH STC BPT MHK VPS LIT MVY CAE ECP FAT ICT MAF MLB EWR BIS LAS OGD FAI ITO JAN IMT UIN HHH XNA DLH HYA DEN EWN RHI SGU ALB CPR GRI LNK OME BOI IAD PSP SBA HOB LAR MEI BRD BRO DRO BMI RKS SEA CMI LAN VEL LRD PBG HYS PSM VLD HNL SLN ERI GST SHV CVG SJC TOL BUF LGA TLH CDC ACT HPN RDD AUS GCC MLI SJU ATW DHN AVL GJT LGB LYH BFL CNY GFK RNO SRQ BJI EYW SBN TTN JAC RST CHS HGR HRL RSW TUL AMA ISP BOS BGM DLG INL PSE MSY PPG DRT GEG BUR SNA GRB GTF IDA GRR LWB JLN PVU EUG PSG ATY GSO MYR PVD OAK EAR BTM COD FAR FSM MQT MSN SCC ESC DCA RFD CID GTR LWS MLU PIB SWO WRG CIU HLN IAG LEX RDM JMS ORF SCE EVV KTN CRW CWA OGS GCK SAV CDV TRI CMH SPN LBF ADK CAK TYR CHO MOB PNS LIH IAH AVP ORD LBE LBL BTV COU MKG AEX BIL SPS ILM PUB SMX PIA GUM BQN RDU HIB MFE PGV MKE XWA BLV ISN SYR HSV LFT ACY MTJ PIT ROW TUS AZO MDW PLN CKB COS OAJ JNU ALO IND EAU KOA GPT MGM OWB SAN BZN GGG SHD YAK ANC DAB JFK PAH SUX CYS GNV MSO OGG PGD PHL DSM SAT SLC STT ASE RAP SBP MSY GEG SNA BUR GRB GTF IDA GRR PVU EUG GSO MYR PVD OAK MSN FSM FAR DCA RFD MLU GTR CID IAG LEX RDM ORF EVV CRW SAV TRI CMH CAK CHO MOB PNS LIH IAH HNL SHV CVG SJC TOL LGA TLH BUF HPN RDD AUS MLI SJU DHN ATW AVL GJT LGB GFK BFL SRQ RNO EYW SBN TTN RST JAC CHS RSW TUL ISP BOS MLB EWR LAS BIS OGD JAN FAI XNA HHH DEN EWN SGU ALB LNK GRI IAD PSP BOI SBA BMI SEA PBG VLD MCI CLT BNA TVC CLL PAE BLI PSC ORH PBI ABQ PIE SDF SCK ACV DAL BDL MRY USA CLE PDX MIA MFR BWI TPA OKC ROA SMF OTH SFB ELM PHX FCA STL ABY PWM DFW ABE MHT GSP MMH FAY STX HDN EGE FSD SWF BQK CSG SUN SFO MEM ELP BHM FLL FNT ATL AZA RIC LCK DAY PHF OMA STC VPS LIT CAE ICT ECP FAT ORD AVP LBE BTV AEX BIL ILM PIA RDU BQN MFE MKE SYR BLV HSV LFT PIT TUS ACY MTJ MDW OAJ COS IND KOA GPT MGM DTW HOU CHA TYS FWA MDT ONT JAX STS LAX MSP MOT HTS BTR MCO AGS ROC SGF SAN BZN ANC JFK DAB GNV MSO PHL PGD OGG DSM SLC SAT STT ASE RAP SBP LWB ATY EAR COD SCC PIB HLN JMS SCE KTN OGS LBF TYR SLN GCC CNY HRL AMA MAF CPR LAR HOB DRO BRO RKS VEL LRD HYS PIR CGI BKG PRC BFF BFM LBB LBL COU PUB SMX XWA ISN CKB JNU BGR SIT OTZ SHD PPG ITO ACK MVY GUM PSG WRG HGR MEI LAN PSM GRK BRW DVL GUC CRP LCH YAK JLN MQT CWA SPN GST ERI UIN DLH CMI DBQ CMX APN SPI MBS LSE MHK MKG AZO ALO EAU PAH SUX DLG PSE BTM LWS CDV ADK CDC HYA OME ART TWF BET EKO HVN PIH AKN ADQ WYS DRT SWO GCK ACT FLG LAW ABI TXK SAF SJT BPT SPS ROW PLN OWB YUM GGG CYS BGM INL ESC CIU BJI IMT RHI BRD ITH ABR HIB LYH PGV

In [0]:


## Let's display the graph vertices - GCP Solution, for Databricks, just display(g.vertices)
g = GraphFrame(vertices, edges)
display(g.vertices.limit(10).toPandas())

## Let's display the graph edges sorted in descending order by weight
display(g.edges.orderBy(col("weight").desc()).limit(10).toPandas())

## Let's display inDegrees sorted in descending order
display(g.inDegrees.orderBy(col("inDegree").desc()).limit(10).toPandas())


## Let's display outDegrees sorted in descending order
display(g.outDegrees.orderBy(col("outDegree").desc()).limit(10).toPandas())



id MSY GEG DRT SNA BUR GRR JLN EUG MYR PVD

src dst weight LGA ORD 28338 ORD LGA 28216 LAX SFO 28176 SFO LAX 28172 LAX JFK 25502 JFK LAX 25396 LAX LAS 23234 LAS LAX 23224 HNL OGG 21442 OGG HNL 21434

id inDegree ORD 187 DFW 183 DEN 177 ATL 168 CLT 136 MSP 130 IAH 120 DTW 116 LAS 114 LAX 110

id outDegree ORD 186 DFW 184 DEN 175 ATL 168 CLT 136 MSP 130 IAH 119 DTW 116 LAS 114 LAX 109

In [0]:
# Calculate pagerank for each node
pr = g.pageRank(resetProbability=0.15, maxIter=10)
display(pr.vertices.orderBy(col("pagerank").desc()).limit(10).toPandas())
# Calculate degree centrality for each node
dc = g.degrees
display(dc.orderBy(col("degree").desc()).limit(10).toPandas())


id pagerank DFW 11.270068461306332 DFW 11.270068461306332 ORD 10.800858701476958 ORD 10.800858701476958 DEN 10.560525947764576 DEN 10.560525947764576 ATL 8.936903999115492 ATL 8.936903999115492 MSP 7.240196442696727 MSP 7.240196442696727

id degree ORD 373 DFW 367 DEN 352 ATL 336 CLT 272 MSP 260 IAH 239 DTW 232 LAS 228 LAX 219

In [0]:
# add pagerank to the dataframe df_1Y_features
df_with_pagerank = df_1Y_features.join(pr.vertices, df_1Y_features.ORIGIN == pr.vertices.id, 'left').drop('id')
# add degree centrality to the dataframe df_1Y_features
df_pr_dc = df_with_pagerank.join(dc, df_1Y_features.ORIGIN == dc.id, 'left').drop('id')






#### Betweeness

In [0]:
edges = (
    df_1Y_features
    .groupBy("ORIGIN", "DEST")
    .count()
    .withColumnRenamed("ORIGIN", "src")
    .withColumnRenamed("DEST", "dst")
    .withColumnRenamed("distance", "weight")
)


# count of number of edges
print(f"There are {edges.count()} edges in our graph.")

nodes = df_1Y_features.select("ORIGIN").distinct().withColumnRenamed("ORIGIN", "id").union(df_1Y_features.select("DEST").distinct().withColumnRenamed("DEST", "id"))



There are 6515 edges in our graph.


In [0]:
import networkx as nx
import pandas as pd
import pyspark.sql.functions as F

# Convert PySpark DataFrame to Pandas (collect to driver)
edges_pd = df_1Y_features.groupBy("ORIGIN", "DEST").agg(
    F.avg("DISTANCE").alias("distance"),
    F.count("*").alias("num_flights")
).toPandas()

# Create directed graph
G = nx.DiGraph()

# Add edges with distance as weight
for _, row in edges_pd.iterrows():
    G.add_edge(
        row['ORIGIN'], 
        row['DEST'], 
        weight=row['distance'],
        num_flights=row['num_flights']
    )

# Calculate betweenness centrality
# weight parameter uses edge weights for shortest path calculation
betweenness = nx.betweenness_centrality(G, weight='weight')

# Convert back to DataFrame
betweenness_df = pd.DataFrame([
    {'airport': k, 'betweenness': v} 
    for k, v in betweenness.items()
])

# Convert to Spark DataFrame and join back
betweenness_spark = spark.createDataFrame(betweenness_df)



In [0]:
df_with_pr_dc_betweenness = df_pr_dc.join(
    betweenness_spark,
    df_pr_dc.ORIGIN == betweenness_spark.airport,
    'left'
).drop('airport')

# handle nulls
pagerank_median = df_with_pr_dc_betweenness.agg(F.expr("percentile_approx(pagerank, 0.5)")).first()[0]
betweenness_median = df_with_pr_dc_betweenness.agg(F.expr("percentile_approx(betweenness, 0.5)")).first()[0]
degree_median = df_with_pr_dc_betweenness.agg(F.expr("percentile_approx(degree, 0.5)")).first()[0]

df_with_pr_dc_betweenness = df_with_pr_dc_betweenness.fillna({
    "pagerank": pagerank_median,
    "betweenness": betweenness_median,
    "degree": degree_median
})


#display number of rows and columns in the new dataframe
print(f"There are {df_with_pr_dc_betweenness.count()} rows and {len(df_with_pr_dc_betweenness.columns)} columns in the new dataframe.")
# display the number of rows and columns in the original dataframe
print(f"There are {df_1Y_features.count()} rows and {len(df_1Y_features.columns)} columns in the original dataframe.")

display(df_with_pr_dc_betweenness, limit=10)



There are 29072928 rows and 50 columns in the new dataframe.
There are 14536464 rows and 47 columns in the original dataframe.


ORIGIN MONTH flight_id prediction_utc origin_obs_utc asof_minutes FL_DATE YEAR QUARTER DAY_OF_MONTH DAY_OF_WEEK OP_CARRIER OP_CARRIER_FL_NUM TAIL_NUM CRS_DEP_TIME DEST DISTANCE DISTANCE_GROUP HourlyDryBulbTemperature HourlyDewPointTemperature HourlyWetBulbTemperature HourlyPrecipitation HourlyWindSpeed HourlyWindDirection HourlyVisibility HourlyRelativeHumidity HourlyStationPressure HourlySeaLevelPressure HourlyAltimeterSetting HourlySkyConditions ORIGIN_TYPE DEST_TYPE DEP_DEL15 DEP_DELAY DEP_HOUR DEP_MINUTE dep_time_bucket is_weekend peak_travel_month peak_travel_hour is_holiday dep_delay_24h_rolling_avg_by_origin dep_delay15_24h_rolling_avg_by_origin dep_delay_24h_rolling_avg_by_origin_carrier dep_delay15_24h_rolling_avg_by_origin_carrier dep_delay_24h_rolling_avg_by_origin_dayofweek dep_delay15_24h_rolling_avg_by_origin_dayofweek pagerank degree betweenness ATL 1 2019-01-07|AA|1828|ATL|PHL 2019-01-07T08:21:00Z 2019-01-07T07:52:00Z 29 2019-01-07 2019 1 7 1 AA 1828 N680AW 521 PHL 666.0 3 45.0 39.0 42.0 0.0 3.0 130.0 10.0 80.0 29.149999618530273 30.25 30.25 15.0 large_airport large_airport 0.0 -7.0 5 21 morning 0 0 0 0 2.6134538152610443 0.09136546184738956 -1.6206896551724137 0.06896551724137931 8.756766002639768 0.16754871700608373 8.936903999115492 336 0.10524683193020144 ATL 1 2019-01-07|AA|1828|ATL|PHL 2019-01-07T08:21:00Z 2019-01-07T07:52:00Z 29 2019-01-07 2019 1 7 1 AA 1828 N680AW 521 PHL 666.0 3 45.0 39.0 42.0 0.0 3.0 130.0 10.0 80.0 29.149999618530273 30.25 30.25 15.0 large_airport large_airport 0.0 -7.0 5 21 morning 0 0 0 0 2.6134538152610443 0.09136546184738956 -1.6206896551724137 0.06896551724137931 8.756766002639768 0.16754871700608373 8.936903999115492 336 0.10524683193020144 ATL 1 2019-01-07|AA|1994|ATL|CLT 2019-01-07T08:39:00Z 2019-01-07T07:52:00Z 47 2019-01-07 2019 1 7 1 AA 1994 N102UW 539 CLT 226.0 1 45.0 39.0 42.0 0.0 3.0 130.0 10.0 80.0 29.149999618530273 30.25 30.25 15.0 large_airport large_airport 0.0 -8.0 5 39 morning 0 0 0 0 2.620100502512563 0.0914572864321608 -1.5357142857142858 0.07142857142857142 -7.0 0.0 8.936903999115492 336 0.10524683193020144 ATL 1 2019-01-07|AA|1994|ATL|CLT 2019-01-07T08:39:00Z 2019-01-07T07:52:00Z 47 2019-01-07 2019 1 7 1 AA 1994 N102UW 539 CLT 226.0 1 45.0 39.0 42.0 0.0 3.0 130.0 10.0 80.0 29.149999618530273 30.25 30.25 15.0 large_airport large_airport 0.0 -8.0 5 39 morning 0 0 0 0 2.620100502512563 0.0914572864321608 -1.5357142857142858 0.07142857142857142 -7.0 0.0 8.936903999115492 336 0.10524683193020144 ATL 1 2019-01-07|B6|996|ATL|BOS 2019-01-07T08:45:00Z 2019-01-07T07:52:00Z 53 2019-01-07 2019 1 7 1 B6 996 N516JB 545 BOS 946.0 4 45.0 39.0 42.0 0.0 3.0 130.0 10.0 80.0 29.149999618530273 30.25 30.25 15.0 large_airport large_airport 0.0 -7.0 5 45 morning 0 0 0 0 2.609437751004016 0.09136546184738956 -1.0 0.2 -7.5 0.0 8.936903999115492 336 0.10524683193020144 ATL 1 2019-01-07|B6|996|ATL|BOS 2019-01-07T08:45:00Z 2019-01-07T07:52:00Z 53 2019-01-07 2019 1 7 1 B6 996 N516JB 545 BOS 946.0 4 45.0 39.0 42.0 0.0 3.0 130.0 10.0 80.0 29.149999618530273 30.25 30.25 15.0 large_airport large_airport 0.0 -7.0 5 45 morning 0 0 0 0 2.609437751004016 0.09136546184738956 -1.0 0.2 -7.5 0.0 8.936903999115492 336 0.10524683193020144 ATL 1 2019-01-07|AA|1151|ATL|MIA 2019-01-07T08:56:00Z 2019-01-07T08:52:00Z 4 2019-01-07 2019 1 7 1 AA 1151 N817NN 556 MIA 594.0 3 50.0 42.0 46.0 0.0 5.0 100.0 10.0 74.0 29.15999984741211 30.270000457763672 30.270000457763672 15.0 large_airport large_airport 0.0 -8.0 5 56 morning 0 0 0 0 2.6231155778894473 0.0914572864321608 -1.7586206896551724 0.06896551724137931 -7.333333333333333 0.0 8.936903999115492 336 0.10524683193020144 ATL 1 2019-01-07|AA|1151|ATL|MIA 2019-01-07T08:56:00Z 2019-01-07T08:52:00Z 4 2019-01-07 2019 1 7 1 AA 1151 N817NN 556 MIA 594.0 3 50.0 42.0 46.0 0.0 5.0 100.0 10.0 74.0 29.15999984741211 30.270000457763672 30.270000457763672 15.0 large_airport large_airport 0.0 -8.0 5 56 morning 0 0 0 0 2.6231155778894473 0.0914572864321608 -1.7586206896551724 

In [0]:
# write to parquet file
df_with_pr_dc_betweenness.write.mode("overwrite").parquet(f"{data_path_12M}df_joined_1Y_features_plus_gf.parquet")
